In [43]:
import pandas as pd
import numpy as np
import warnings

warnings.filterwarnings("ignore")

data = pd.read_csv("model_df.csv", index_col=0)
data['date'] = pd.to_datetime(data['Date'])
data = data.sort_values(by="Date", ascending=True)
data['home_1h_score'] = data['Home 1H Points']
data['away_1h_score'] = data['Away 1H Points']
data['home_score'] = data['Home Full Points']
data['away_score'] = data['Away Full Points']
data['total'] = data['home_score'] + data['away_score']
data['home_2h_score'] = data['home_score'] - data['home_1h_score']
data['away_2h_score'] = data['away_score'] - data['away_1h_score']
data['home_team'] = data['Team_home']
data['away_team'] = data['Team_away']
data['margin'] = data['home_score'] - data['away_score']

In [44]:
data["home_opp_score_rank"] = data["Rk_away"] - data['home_score']
data['away_opp_score_rank'] = data['Rk_home'] - data['away_score']
data['home_sos'] = data['Rk_away']
data['away_sos'] = data['Rk_home']

In [45]:
# Melt data to unify home and away records with opponent scores
home_df = data[['date', 'home_team', 'home_score', 'AdjT_Rk_away', 'AdjO_Rk_away', 'AdjD_Rk_away', 'away_score', 'home_sos', "home_opp_score_rank"]].rename(columns={
    'home_team': 'team', 'home_score': 'score', 'away_score': 'opponent_score', 'home_sos': 'sos', "home_opp_score_rank": "opp_score_rank", 'AdjT_Rk_away': "opp_tempo", 'AdjO_Rk_away': 'opp_off', 'AdjD_Rk_away':"opp_def",
})
away_df = data[['date', 'away_team', 'away_score', 'home_score','AdjT_Rk_home', 'AdjO_Rk_home', 'AdjD_Rk_home','away_sos', "away_opp_score_rank"]].rename(columns={
    'away_team': 'team', 'away_score': 'score', 'home_score': 'opponent_score','away_sos': 'sos', "away_opp_score_rank": "opp_score_rank",'AdjT_Rk_home': "opp_tempo", 'AdjO_Rk_home': 'opp_off', 'AdjD_Rk_home':"opp_def"
})
games = pd.concat([home_df, away_df])
games.sort_values(by=['team', 'date'], inplace=True)
games['score_diff'] = games['score'] - games['opponent_score']

In [46]:
rank_columns = ['opp_tempo', 'opp_off', 'opp_def']
bin_size = 121

for col in rank_columns:
    # Define bin edges and labels
    bin_edges = list(range(1, 363 + 1, bin_size))  # Ensure the upper edge includes the maximum value
    bin_labels = [f"{bin_edges[i]}-{bin_edges[i + 1] - 1}" for i in range(len(bin_edges) - 1)]

    # Bin the column into ranges
    games[f'{col}_bin'] = pd.cut(games[col], bins=bin_edges, labels=bin_labels, right=False)

    # Create binary columns for each bin
    for label in bin_labels:
        games[f'{col}_bin_{label}'] = (games[f'{col}_bin'] == label).astype(int)

In [47]:
# Define the rolling windows
rolling_windows = [1, 3, 7]

# Calculate rolling averages for each window and store as separate columns
for window in rolling_windows:
    games[f'rolling_avg_score_{window}'] = (
        games.groupby('team')['score']
        .shift()
        .rolling(window=window, min_periods=1)
        .mean()
    )
    games[f'rolling_avg_score_allowed_{window}'] = (
        games.groupby('team')['opponent_score']
        .shift()
        .rolling(window=window, min_periods=1)
        .mean()
    )
    games[f'rolling_sos_{window}'] = (
        games.groupby('team')['sos']
        .shift()
        .rolling(window=window, min_periods=1)
        .mean()
    )
    games[f'rolling_opp_score_rank_{window}'] = (
        games.groupby('team')['opp_score_rank']
        .shift()
        .rolling(window=window, min_periods=1)
        .mean()
    )
    games[f'rolling_score_diff_{window}'] = (
        games.groupby('team')['score_diff']
        .shift()
        .rolling(window=window, min_periods=1)
        .mean()
    )

# Avoid duplicate indices when calculating rolling average score differential for bins
for col in rank_columns:
    bin_labels = [f"{bin_edges[i]}-{bin_edges[i + 1] - 1}" for i in range(len(bin_edges) - 1)]

    for label in bin_labels:
        for window in rolling_windows:
            # Ensure group indices are unique before applying transformations
            rolling_diff = (
                games.groupby('team', group_keys=False)
                .apply(
                    lambda group: group.loc[group[f'{col}_bin_{label}'] == 1, 'score_diff']
                    .shift()
                    .rolling(window=window, min_periods=1)
                    .mean()
                )
            )
            # Assign the rolling results back to the DataFrame
            games[f'rolling_avg_score_diff_{col}_bin_{label}_{window}'] = rolling_diff.reset_index(drop=True)

# Calculate days since the last game
games['days_since_last_game'] = games.groupby('team')['date'].diff().dt.days

In [49]:
columns_to_keep = ['date', 'team', 'days_since_last_game'] + \
                  [f'rolling_avg_score_{w}' for w in rolling_windows] + \
                  [f'rolling_avg_score_allowed_{w}' for w in rolling_windows] + \
                  [f'rolling_sos_{w}' for w in rolling_windows] + \
                  [f'rolling_score_diff_{w}' for w in rolling_windows] + \
                  [f'rolling_opp_score_rank_{w}' for w in rolling_windows] + \
                  [f'rolling_avg_score_diff_{col}_bin_{label}_{w}'
                   for col in rank_columns
                   for label in bin_labels
                   for w in rolling_windows]
games = games[columns_to_keep]

# Merge rolling features back to the original data on home and away team sides
# First, join for home team
data = data.merge(
    games.rename(columns={
        'team': 'home_team',
        **{f'rolling_avg_score_{w}': f'home_rolling_avg_score_{w}' for w in rolling_windows},
        **{f'rolling_avg_score_allowed_{w}': f'home_rolling_avg_score_allowed_{w}' for w in rolling_windows},
        **{f'rolling_sos_{w}': f'home_rolling_sos_{w}' for w in rolling_windows},
        **{f'rolling_score_diff_{w}': f'home_rolling_score_diff_{w}' for w in rolling_windows},
        **{f'rolling_opp_score_rank_{w}': f'home_rolling_opp_score_rank_{w}' for w in rolling_windows},
        **{f'rolling_avg_score_diff_{col}_bin_{label}_{w}': f'home_rolling_avg_score_diff_{col}_bin_{label}_{w}'
           for col in rank_columns
           for label in bin_labels
           for w in rolling_windows},
        'days_since_last_game': 'home_days_since_last_game'
    }),
    on=['date', 'home_team'],
    how='left'
)

# Then, join for away team
data = data.merge(
    games.rename(columns={
        'team': 'away_team',
        **{f'rolling_avg_score_{w}': f'away_rolling_avg_score_{w}' for w in rolling_windows},
        **{f'rolling_avg_score_allowed_{w}': f'away_rolling_avg_score_allowed_{w}' for w in rolling_windows},
        **{f'rolling_sos_{w}': f'away_rolling_sos_{w}' for w in rolling_windows},
        **{f'rolling_score_diff_{w}': f'away_rolling_score_diff_{w}' for w in rolling_windows},
        **{f'rolling_opp_score_rank_{w}': f'away_rolling_opp_score_rank_{w}' for w in rolling_windows},
        **{f'rolling_avg_score_diff_{col}_bin_{label}_{w}': f'away_rolling_avg_score_diff_{col}_bin_{label}_{w}'
           for col in rank_columns
           for label in bin_labels
           for w in rolling_windows},
        'days_since_last_game': 'away_days_since_last_game'
    }),
    on=['date', 'away_team'],
    how='left'
)

In [52]:
df = data.dropna()

In [1]:
import pandas as pd
import numpy as np
df = pd.read_csv("train.csv")

/var/folders/0b/h0zc244107jg60tttkl4r0kw0000gn/T/ipykernel_501/2192547051.py:3: DtypeWarning: Columns (18,69) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("train.csv")


In [2]:
df['margin'] = df['home_score'] - df['away_score']
df['home_win'] = np.where(df['home_score'] > df['away_score'], 1, 0)
df['away_win'] = np.where(df['away_score'] > df['home_score'], 1, 0)

### LIGHTGBM NO OUTLIER REDUCTION

In [57]:
import optuna
import numpy as np
from sklearn.ensemble import IsolationForest
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error
from sklearn.preprocessing import LabelEncoder
import lightgbm as lgb
import joblib
import os
import pandas as pd

os.makedirs("lgb_models", exist_ok=True)

high_outlier_thresholds = {'home_score': 91, 'away_score': 78, 'total': 167}
low_outlier_thresholds = {'home_score': 56, 'away_score': 52, 'total': 118}

for target_column in ['home_score', 'away_score', 'total', 'margin']:
    categorical_columns = ['Conf_home', 'Conf_away']

    model_df = df[[target_column, 'Date', 
       'Rk_home', 'Conf_home', 'AdjEM_home', 'AdjO_home',
       'AdjO_Rk_home', 'AdjD_home', 'AdjD_Rk_home', 'AdjT_home',
       'AdjT_Rk_home','Rk_rolling_1_home',
       'AdjEM_rolling_1_home', 'AdjO_rolling_1_home',
       'AdjO_Rk_rolling_1_home', 'AdjD_rolling_1_home',
       'AdjD_Rk_rolling_1_home', 'AdjT_rolling_1_home',
       'AdjT_Rk_rolling_1_home', 'Rk_rolling_3_home',
       'AdjEM_rolling_3_home', 'AdjO_rolling_3_home',
       'AdjO_Rk_rolling_3_home', 'AdjD_rolling_3_home',
       'AdjD_Rk_rolling_3_home', 'AdjT_rolling_3_home',
       'AdjT_Rk_rolling_3_home', 'Rk_rolling_5_home',
       'AdjEM_rolling_5_home', 'AdjO_rolling_5_home',
       'AdjO_Rk_rolling_5_home', 'AdjD_rolling_5_home',
       'AdjD_Rk_rolling_5_home', 'AdjT_rolling_5_home',
       'AdjT_Rk_rolling_5_home', 'Rk_rolling_10_home',
       'AdjEM_rolling_10_home', 'AdjO_rolling_10_home',
       'AdjO_Rk_rolling_10_home', 'AdjD_rolling_10_home',
       'AdjD_Rk_rolling_10_home', 'AdjT_rolling_10_home',
       'AdjT_Rk_rolling_10_home', 'Rk_rolling_20_home',
       'AdjEM_rolling_20_home', 'AdjO_rolling_20_home',
       'AdjO_Rk_rolling_20_home', 'AdjD_rolling_20_home',
       'AdjD_Rk_rolling_20_home', 'AdjT_rolling_20_home',
       'AdjT_Rk_rolling_20_home', 'Rk_away', 'Conf_away',
       'AdjEM_away', 'AdjO_away', 'AdjO_Rk_away', 'AdjD_away',
       'AdjD_Rk_away', 'AdjT_away', 'AdjT_Rk_away',
       'Rk_rolling_1_away', 'AdjEM_rolling_1_away', 'AdjO_rolling_1_away',
       'AdjO_Rk_rolling_1_away', 'AdjD_rolling_1_away',
       'AdjD_Rk_rolling_1_away', 'AdjT_rolling_1_away',
       'AdjT_Rk_rolling_1_away', 'Rk_rolling_3_away',
       'AdjEM_rolling_3_away', 'AdjO_rolling_3_away',
       'AdjO_Rk_rolling_3_away', 'AdjD_rolling_3_away',
       'AdjD_Rk_rolling_3_away', 'AdjT_rolling_3_away',
       'AdjT_Rk_rolling_3_away', 'Rk_rolling_5_away',
       'AdjEM_rolling_5_away', 'AdjO_rolling_5_away',
       'AdjO_Rk_rolling_5_away', 'AdjD_rolling_5_away',
       'AdjD_Rk_rolling_5_away', 'AdjT_rolling_5_away',
       'AdjT_Rk_rolling_5_away', 'Rk_rolling_10_away',
       'AdjEM_rolling_10_away', 'AdjO_rolling_10_away',
       'AdjO_Rk_rolling_10_away', 'AdjD_rolling_10_away',
       'AdjD_Rk_rolling_10_away', 'AdjT_rolling_10_away',
       'AdjT_Rk_rolling_10_away', 'Rk_rolling_20_away',
       'AdjEM_rolling_20_away', 'AdjO_rolling_20_away',
       'AdjO_Rk_rolling_20_away', 'AdjD_rolling_20_away',
       'AdjD_Rk_rolling_20_away', 'AdjT_rolling_20_away',
       'AdjT_Rk_rolling_20_away', 'home_sos',
       'away_sos', 'home_days_since_last_game',
       'home_rolling_avg_score_1', 'home_rolling_avg_score_3',
       'home_rolling_avg_score_7', 'home_rolling_avg_score_allowed_1',
       'home_rolling_avg_score_allowed_3',
       'home_rolling_avg_score_allowed_7', 'home_rolling_sos_1',
       'home_rolling_sos_3', 'home_rolling_sos_7',
       'home_rolling_score_diff_1', 'home_rolling_score_diff_3',
       'home_rolling_score_diff_7', 'home_rolling_opp_score_rank_1',
       'home_rolling_opp_score_rank_3', 'home_rolling_opp_score_rank_7',
       'home_rolling_avg_score_diff_opp_tempo_bin_1-121_1',
       'home_rolling_avg_score_diff_opp_tempo_bin_1-121_3',
       'home_rolling_avg_score_diff_opp_tempo_bin_1-121_7',
       'home_rolling_avg_score_diff_opp_tempo_bin_122-242_1',
       'home_rolling_avg_score_diff_opp_tempo_bin_122-242_3',
       'home_rolling_avg_score_diff_opp_tempo_bin_122-242_7',
       'home_rolling_avg_score_diff_opp_off_bin_1-121_1',
       'home_rolling_avg_score_diff_opp_off_bin_1-121_3',
       'home_rolling_avg_score_diff_opp_off_bin_1-121_7',
       'home_rolling_avg_score_diff_opp_off_bin_122-242_1',
       'home_rolling_avg_score_diff_opp_off_bin_122-242_3',
       'home_rolling_avg_score_diff_opp_off_bin_122-242_7',
       'home_rolling_avg_score_diff_opp_def_bin_1-121_1',
       'home_rolling_avg_score_diff_opp_def_bin_1-121_3',
       'home_rolling_avg_score_diff_opp_def_bin_1-121_7',
       'home_rolling_avg_score_diff_opp_def_bin_122-242_1',
       'home_rolling_avg_score_diff_opp_def_bin_122-242_3',
       'home_rolling_avg_score_diff_opp_def_bin_122-242_7',
       'away_days_since_last_game', 'away_rolling_avg_score_1',
       'away_rolling_avg_score_3', 'away_rolling_avg_score_7',
       'away_rolling_avg_score_allowed_1',
       'away_rolling_avg_score_allowed_3',
       'away_rolling_avg_score_allowed_7', 'away_rolling_sos_1',
       'away_rolling_sos_3', 'away_rolling_sos_7',
       'away_rolling_score_diff_1', 'away_rolling_score_diff_3',
       'away_rolling_score_diff_7', 'away_rolling_opp_score_rank_1',
       'away_rolling_opp_score_rank_3', 'away_rolling_opp_score_rank_7',
       'away_rolling_avg_score_diff_opp_tempo_bin_1-121_1',
       'away_rolling_avg_score_diff_opp_tempo_bin_1-121_3',
       'away_rolling_avg_score_diff_opp_tempo_bin_1-121_7',
       'away_rolling_avg_score_diff_opp_tempo_bin_122-242_1',
       'away_rolling_avg_score_diff_opp_tempo_bin_122-242_3',
       'away_rolling_avg_score_diff_opp_tempo_bin_122-242_7',
       'away_rolling_avg_score_diff_opp_off_bin_1-121_1',
       'away_rolling_avg_score_diff_opp_off_bin_1-121_3',
       'away_rolling_avg_score_diff_opp_off_bin_1-121_7',
       'away_rolling_avg_score_diff_opp_off_bin_122-242_1',
       'away_rolling_avg_score_diff_opp_off_bin_122-242_3',
       'away_rolling_avg_score_diff_opp_off_bin_122-242_7',
       'away_rolling_avg_score_diff_opp_def_bin_1-121_1',
       'away_rolling_avg_score_diff_opp_def_bin_1-121_3',
       'away_rolling_avg_score_diff_opp_def_bin_1-121_7',
       'away_rolling_avg_score_diff_opp_def_bin_122-242_1',
       'away_rolling_avg_score_diff_opp_def_bin_122-242_3',
       'away_rolling_avg_score_diff_opp_def_bin_122-242_7']]
    
    for cat_col in categorical_columns:
        le = LabelEncoder()
        model_df[cat_col] = le.fit_transform(df[cat_col])

    iso_forest = IsolationForest(contamination=0.1, random_state=42)
    iso_forest.fit(model_df.drop([target_column, 'Date'], axis=1))
    
    model_df['outlier_score'] = iso_forest.decision_function(model_df.drop([target_column, 'Date'], axis=1))
    model_df['date'] = pd.to_datetime(df['Date'])
    model_df = model_df.sort_values(by='date')

    test_ratio = 0.2
    split_index = int(len(model_df) * (1 - test_ratio))

    train_data = model_df.iloc[:split_index]
    test_data = model_df.iloc[split_index:]

    X_train = train_data.drop(columns=['date', 'Date', target_column])
    y_train = train_data[target_column]

    X_test = test_data.drop(columns=['date', 'Date', target_column])
    y_test = test_data[target_column]

    def objective_lgb(trial):
        param = {
            'objective': 'regression',
            'metric': 'rmse',
            'boosting_type': 'gbdt',
            'max_depth': trial.suggest_int('max_depth', -1, 10),
            'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 0.3),
            'n_estimators': trial.suggest_int('n_estimators', 100, 1500),
            'num_leaves': trial.suggest_int('num_leaves', 20, 150),
            'min_child_samples': trial.suggest_int('min_child_samples', 5, 50),
            'subsample': trial.suggest_float('subsample', 0.5, 1.0),
            'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
            'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 5.0),
            'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 5.0),
        }
        
        train_data = lgb.Dataset(X_train, label=y_train)
        valid_data = lgb.Dataset(X_test, label=y_test)
        
        model = lgb.train(
            params=param,
            train_set=train_data,
            valid_sets=[train_data, valid_data],
            valid_names=["train", "valid"]        )
        
        y_pred = model.predict(X_test, num_iteration=model.best_iteration)
        rmse = mean_squared_error(y_test, y_pred, squared=False)
        return rmse



    study_lgb = optuna.create_study(direction='minimize')
    study_lgb.optimize(objective_lgb, n_trials=50)
    print(f"Best LightGBM parameters for {target_column}: {study_lgb.best_params}")

    best_lgb = lgb.LGBMRegressor(**study_lgb.best_params)
    best_lgb.fit(X_train, y_train)
    y_pred_lgb = best_lgb.predict(X_test)

    best_model_filename = f"lgb_models/{target_column}_best_model.joblib"
    joblib.dump(best_lgb, best_model_filename)

    def display_metrics(y_true, y_pred, model_name):
        r2 = r2_score(y_true, y_pred)
        mae = mean_absolute_error(y_true, y_pred)
        rmse = mean_squared_error(y_true, y_pred, squared=False)
        print(f"{model_name} R^2: {r2:.4f}")
        print(f"{model_name} MAE: {mae:.4f}")
        print(f"{model_name} RMSE: {rmse:.4f}")

    display_metrics(y_test, y_pred_lgb, "LightGBM with Outlier Score Feature")

[I 2024-11-21 21:56:09,404] A new study created in memory with name: no-name-31e51ed2-a97c-4aff-aada-e26a5ebac4fd


[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003267 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 37940
[LightGBM] [Info] Number of data points in the train set: 12399, number of used features: 169
[LightGBM] [Info] Start training from score 75.011533
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive

[I 2024-11-21 21:56:11,071] Trial 0 finished with value: 10.242925244688543 and parameters: {'max_depth': 2, 'learning_rate': 0.213724231856149, 'n_estimators': 1166, 'num_leaves': 50, 'min_child_samples': 24, 'subsample': 0.9746548968257516, 'colsample_bytree': 0.7004021301236947, 'reg_alpha': 3.929451847336554, 'reg_lambda': 0.8476246903633039}. Best is trial 0 with value: 10.242925244688543.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002865 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 37940
[LightGBM] [Info] Number of data points in the train set: 12399, number of used features: 169
[LightGBM] [Info] Start training from score 75.011533
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive

[I 2024-11-21 21:56:18,745] Trial 1 finished with value: 9.73995486958958 and parameters: {'max_depth': 8, 'learning_rate': 0.010077651416027785, 'n_estimators': 1015, 'num_leaves': 83, 'min_child_samples': 37, 'subsample': 0.7264194260179396, 'colsample_bytree': 0.6859685101030504, 'reg_alpha': 4.18477632229433, 'reg_lambda': 4.340750678031889}. Best is trial 1 with value: 9.73995486958958.


...

[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.005689 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 37940
[LightGBM] [Info] Number of data points in the train set: 12399, number of used features: 169
[LightGBM] [Info] Start training from score 11.917574
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive

[I 2024-11-21 22:09:29,559] Trial 48 finished with value: 8.36796110383171 and parameters: {'max_depth': 7, 'learning_rate': 0.011494726173807014, 'n_estimators': 276, 'num_leaves': 102, 'min_child_samples': 22, 'subsample': 0.5936980696919184, 'colsample_bytree': 0.631532593963928, 'reg_alpha': 3.296751064702764, 'reg_lambda': 2.357742484784777}. Best is trial 41 with value: 8.289247326572998.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-11-21 22:09:32,606] Trial 49 finished with value: 8.303611902793087 and parameters: {'max_depth': 9, 'learning_rate': 0.013663310100697235, 'n_estimators': 612, 'num_leaves': 27, 'min_child_samples': 41, 'subsample': 0.5493030506085124, 'colsample_bytree': 0.6712911758496289, 'reg_alpha': 4.8115551898331566, 'reg_lambda': 1.2052449876351163}. Best is trial 41 with value: 8.289247326572998.


Best LightGBM parameters for margin: {'max_depth': 9, 'learning_rate': 0.016202268325081547, 'n_estimators': 508, 'num_leaves': 32, 'min_child_samples': 38, 'subsample': 0.5372531657324826, 'colsample_bytree': 0.6503856560422789, 'reg_alpha': 4.178774741626879, 'reg_lambda': 2.0198052064847136}
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.006523 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 37940
[LightGBM] [Info] Number of data points in the train set: 12399, number of used features: 169
[LightGBM] [Info] Start training from score 11.917574
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gai

### LIGHTGBM OUTLIER REDUCTION

In [62]:
import optuna
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error
from sklearn.preprocessing import LabelEncoder
import lightgbm as lgb
import joblib
import os
import pandas as pd

os.makedirs("lgb_models", exist_ok=True)

# Define thresholds for capping target values
target_outlier_thresholds = {
    'home_score': {'low': 50, 'high': 100},
    'away_score': {'low': 50, 'high': 100},
    'total': {'low': 110, 'high': 180},
    'margin': {'low': -30, 'high': 30},
}

# Specify the features and target column for each target
for target_column in ['margin', 'total', 'away_score', 'home_score']:
    categorical_columns = ['Conf_home', 'Conf_away']  # Update to actual categorical columns

    # Prepare data
    model_df = df[[target_column, 'Date','Rk_home','Conf_home', 'AdjEM_home', 'AdjO_home',
       'AdjO_Rk_home', 'AdjD_home', 'AdjD_Rk_home', 'AdjT_home',
       'AdjT_Rk_home', 'Rk_rolling_1_home',
       'AdjEM_rolling_1_home', 'AdjO_rolling_1_home',
       'AdjO_Rk_rolling_1_home', 'AdjD_rolling_1_home',
       'AdjD_Rk_rolling_1_home', 'AdjT_rolling_1_home',
       'AdjT_Rk_rolling_1_home', 'Rk_rolling_3_home',
       'AdjEM_rolling_3_home', 'AdjO_rolling_3_home',
       'AdjO_Rk_rolling_3_home', 'AdjD_rolling_3_home',
       'AdjD_Rk_rolling_3_home', 'AdjT_rolling_3_home',
       'AdjT_Rk_rolling_3_home', 'Rk_rolling_5_home',
       'AdjEM_rolling_5_home', 'AdjO_rolling_5_home',
       'AdjO_Rk_rolling_5_home', 'AdjD_rolling_5_home',
       'AdjD_Rk_rolling_5_home', 'AdjT_rolling_5_home',
       'AdjT_Rk_rolling_5_home', 'Rk_rolling_10_home',
       'AdjEM_rolling_10_home', 'AdjO_rolling_10_home',
       'AdjO_Rk_rolling_10_home', 'AdjD_rolling_10_home',
       'AdjD_Rk_rolling_10_home', 'AdjT_rolling_10_home',
       'AdjT_Rk_rolling_10_home', 'Rk_rolling_20_home',
       'AdjEM_rolling_20_home', 'AdjO_rolling_20_home',
       'AdjO_Rk_rolling_20_home', 'AdjD_rolling_20_home',
       'AdjD_Rk_rolling_20_home', 'AdjT_rolling_20_home',
       'AdjT_Rk_rolling_20_home', 'Rk_away', 'Conf_away',
       'AdjEM_away', 'AdjO_away', 'AdjO_Rk_away', 'AdjD_away',
       'AdjD_Rk_away', 'AdjT_away', 'AdjT_Rk_away',
       'Rk_rolling_1_away', 'AdjEM_rolling_1_away', 'AdjO_rolling_1_away',
       'AdjO_Rk_rolling_1_away', 'AdjD_rolling_1_away',
       'AdjD_Rk_rolling_1_away', 'AdjT_rolling_1_away',
       'AdjT_Rk_rolling_1_away', 'Rk_rolling_3_away',
       'AdjEM_rolling_3_away', 'AdjO_rolling_3_away',
       'AdjO_Rk_rolling_3_away', 'AdjD_rolling_3_away',
       'AdjD_Rk_rolling_3_away', 'AdjT_rolling_3_away',
       'AdjT_Rk_rolling_3_away', 'Rk_rolling_5_away',
       'AdjEM_rolling_5_away', 'AdjO_rolling_5_away',
       'AdjO_Rk_rolling_5_away', 'AdjD_rolling_5_away',
       'AdjD_Rk_rolling_5_away', 'AdjT_rolling_5_away',
       'AdjT_Rk_rolling_5_away', 'Rk_rolling_10_away',
       'AdjEM_rolling_10_away', 'AdjO_rolling_10_away',
       'AdjO_Rk_rolling_10_away', 'AdjD_rolling_10_away',
       'AdjD_Rk_rolling_10_away', 'AdjT_rolling_10_away',
       'AdjT_Rk_rolling_10_away', 'Rk_rolling_20_away',
       'AdjEM_rolling_20_away', 'AdjO_rolling_20_away',
       'AdjO_Rk_rolling_20_away', 'AdjD_rolling_20_away',
       'AdjD_Rk_rolling_20_away', 'AdjT_rolling_20_away',
       'AdjT_Rk_rolling_20_away',  'home_sos',
       'away_sos', 'home_days_since_last_game',
       'home_rolling_avg_score_1', 'home_rolling_avg_score_3',
       'home_rolling_avg_score_7', 'home_rolling_sos_1',
       'home_rolling_sos_3', 'home_rolling_sos_7',
       'home_rolling_avg_score_allowed_1',
       'home_rolling_avg_score_allowed_3',
       'home_rolling_avg_score_allowed_7',
       'home_rolling_opp_score_rank_1', 'home_rolling_opp_score_rank_3',
       'home_rolling_opp_score_rank_7', 'away_days_since_last_game',
       'away_rolling_avg_score_1', 'away_rolling_avg_score_3',
       'away_rolling_avg_score_7', 'away_rolling_sos_1',
       'away_rolling_sos_3', 'away_rolling_sos_7',
       'away_rolling_avg_score_allowed_1',
       'away_rolling_avg_score_allowed_3',
       'away_rolling_avg_score_allowed_7',
       'away_rolling_opp_score_rank_1', 'away_rolling_opp_score_rank_3',
       'away_rolling_opp_score_rank_7']]

    # Handle outliers in the target column using capping
    low_threshold = target_outlier_thresholds[target_column]['low']
    high_threshold = target_outlier_thresholds[target_column]['high']
    model_df[target_column] = model_df[target_column].clip(lower=low_threshold, upper=high_threshold)

    # Encode categorical columns
    for cat_col in categorical_columns:
        le = LabelEncoder()
        model_df[cat_col] = le.fit_transform(df[cat_col])

    # Ensure the dataframe is sorted by the "date" column
    model_df['date'] = pd.to_datetime(df['Date'])  # Convert to datetime if not already
    model_df = model_df.sort_values(by='date')

    # Define the split ratio
    test_ratio = 0.2  # 20% of the data will be used for testing
    split_index = int(len(model_df) * (1 - test_ratio))

    # Split data into training and testing sets
    train_data = model_df.iloc[:split_index]
    test_data = model_df.iloc[split_index:]

    # Separate features and target
    X_train = train_data.drop(columns=['date', 'Date', target_column])
    y_train = train_data[target_column]

    X_test = test_data.drop(columns=['date', 'Date', target_column])
    y_test = test_data[target_column]

    # Define Optuna objective function for LightGBM
    def objective_lgb(trial):
        param = {
            'objective': 'regression',
            'metric': 'rmse',
            'boosting_type': 'gbdt',
            'max_depth': trial.suggest_int('max_depth', -1, 10),
            'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 0.3),
            'n_estimators': trial.suggest_int('n_estimators', 100, 2000),
            'num_leaves': trial.suggest_int('num_leaves', 20, 150),
            'min_child_samples': trial.suggest_int('min_child_samples', 5, 50),
            'subsample': trial.suggest_float('subsample', 0.5, 1.0),
            'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
            'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 5.0),
            'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 5.0),
        }
        
        # Convert training and testing sets to lightgbm.Dataset
        train_data = lgb.Dataset(X_train, label=y_train)
        valid_data = lgb.Dataset(X_test, label=y_test)
        
        # Train LightGBM model with early stopping
        model = lgb.train(
            params=param,
            train_set=train_data,
            valid_sets=[train_data, valid_data],
            valid_names=["train", "valid"],
        )
        
        # Use best iteration for prediction
        y_pred = model.predict(X_test, num_iteration=model.best_iteration)
        rmse = mean_squared_error(y_test, y_pred, squared=False)
        return rmse

    # Optimize LightGBM with Optuna
    study_lgb = optuna.create_study(direction='minimize')
    study_lgb.optimize(objective_lgb, n_trials=50)
    print(f"Best LightGBM parameters for {target_column}: {study_lgb.best_params}")

    # Train the best LightGBM model with the optimized parameters
    best_lgb = lgb.LGBMRegressor(**study_lgb.best_params)
    best_lgb.fit(X_train, y_train)
    y_pred_lgb = best_lgb.predict(X_test)

    # Save the final best model for this target column
    best_model_filename = f"lgb_models/{target_column}_best_model.joblib"
    joblib.dump(best_lgb, best_model_filename)

    # Define a function to calculate and display metrics
    def display_metrics(y_true, y_pred, model_name):
        r2 = r2_score(y_true, y_pred)
        mae = mean_absolute_error(y_true, y_pred)
        rmse = mean_squared_error(y_true, y_pred, squared=False)
        print(f"{model_name} R^2: {r2:.4f}")
        print(f"{model_name} MAE: {mae:.4f}")
        print(f"{model_name} RMSE: {rmse:.4f}")

    # Display metrics for the LightGBM model
    display_metrics(y_test, y_pred_lgb, "LightGBM with Capped Targets")

[I 2024-11-22 08:00:06,002] A new study created in memory with name: no-name-246d25bb-a638-4c3c-a031-484546ab076b


[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.013804 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 30540
[LightGBM] [Info] Number of data points in the train set: 55835, number of used features: 126
[LightGBM] [Info] Start training from score -0.004191


[I 2024-11-22 08:00:20,918] Trial 0 finished with value: 11.794189331037376 and parameters: {'max_depth': 0, 'learning_rate': 0.18373481246223472, 'n_estimators': 928, 'num_leaves': 61, 'min_child_samples': 22, 'subsample': 0.9765909567114052, 'colsample_bytree': 0.7223046476596681, 'reg_alpha': 3.807303491886786, 'reg_lambda': 1.8642158978293506}. Best is trial 0 with value: 11.794189331037376.


[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.012478 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 30540
[LightGBM] [Info] Number of data points in the train set: 55835, number of used features: 126
[LightGBM] [Info] Start training from score -0.004191


[I 2024-11-22 08:00:26,432] Trial 1 finished with value: 11.159007201491523 and parameters: {'max_depth': 1, 'learning_rate': 0.01698889754123644, 'n_estimators': 1751, 'num_leaves': 88, 'min_child_samples': 20, 'subsample': 0.8459178804084735, 'colsample_bytree': 0.535642473259419, 'reg_alpha': 0.552887898793446, 'reg_lambda': 1.6958827815119693}. Best is trial 1 with value: 11.159007201491523.


...

[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.068902 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 30540
[LightGBM] [Info] Number of data points in the train set: 55835, number of used features: 126
[LightGBM] [Info] Start training from score -0.004191
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive

[I 2024-11-22 08:02:20,970] Trial 9 finished with value: 11.135205923876894 and parameters: {'max_depth': 3, 'learning_rate': 0.020470897341601325, 'n_estimators': 1673, 'num_leaves': 32, 'min_child_samples': 34, 'subsample': 0.9521382642026008, 'colsample_bytree': 0.6196539310427356, 'reg_alpha': 3.113632720871548, 'reg_lambda': 2.5512400064404894}. Best is trial 7 with value: 11.134428645865617.


[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.014062 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 30540
[LightGBM] [Info] Number of data points in the train set: 55835, number of used features: 126
[LightGBM] [Info] Start training from score -0.004191
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive

[I 2024-11-22 08:02:48,379] Trial 10 finished with value: 11.279301191951756 and parameters: {'max_depth': 10, 'learning_rate': 0.03875113223176095, 'n_estimators': 770, 'num_leaves': 145, 'min_child_samples': 50, 'subsample': 0.837428577893223, 'colsample_bytree': 0.798054529522819, 'reg_alpha': 2.300832203727409, 'reg_lambda': 4.932868716889569}. Best is trial 7 with value: 11.134428645865617.
[W 2024-11-22 08:02:48,882] Trial 11 failed with parameters: {'max_depth': 4, 'learning_rate': 0.01813579353960066, 'n_estimators': 1540, 'num_leaves': 48, 'min_child_samples': 36, 'subsample': 0.9068317625867457, 'colsample_bytree': 0.6051409272933892, 'reg_alpha': 3.0874090524739928, 'reg_lambda': 2.7548597753822968} because of the following error: KeyboardInterrupt().
Traceback (most recent call last):
  File "/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/optuna/study/_optimize.py", line 200, in _run_trial
    value_or_values = func(trial)
  File "/var/folde

KeyboardInterrupt: 

### XGBOOST OUTLIER REDUCTION

In [3]:
import optuna
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, f1_score, roc_auc_score, matthews_corrcoef
from sklearn.preprocessing import LabelEncoder
import xgboost as xgb
import joblib
import os
import pandas as pd

import warnings
warnings.filterwarnings("ignore")

os.makedirs("xgb_models", exist_ok=True)

# Specify the features and target column for each target
for target_column in ['home_win', 'away_win']:
    categorical_columns = ['Conf_home', 'Conf_away']  # Update to actual categorical columns

    # Prepare data
    model_df = df[[target_column, 'Date','Rk_home','Conf_home', 'AdjEM_home', 'AdjO_home',
       'AdjO_Rk_home', 'AdjD_home', 'AdjD_Rk_home', 'AdjT_home',
       'AdjT_Rk_home', 'Rk_rolling_1_home',
       'AdjEM_rolling_1_home', 'AdjO_rolling_1_home',
       'AdjO_Rk_rolling_1_home', 'AdjD_rolling_1_home',
       'AdjD_Rk_rolling_1_home', 'AdjT_rolling_1_home',
       'AdjT_Rk_rolling_1_home', 'Rk_rolling_3_home',
       'AdjEM_rolling_3_home', 'AdjO_rolling_3_home',
       'AdjO_Rk_rolling_3_home', 'AdjD_rolling_3_home',
       'AdjD_Rk_rolling_3_home', 'AdjT_rolling_3_home',
       'AdjT_Rk_rolling_3_home', 'Rk_rolling_5_home',
       'AdjEM_rolling_5_home', 'AdjO_rolling_5_home',
       'AdjO_Rk_rolling_5_home', 'AdjD_rolling_5_home',
       'AdjD_Rk_rolling_5_home', 'AdjT_rolling_5_home',
       'AdjT_Rk_rolling_5_home', 'Rk_rolling_10_home',
       'AdjEM_rolling_10_home', 'AdjO_rolling_10_home',
       'AdjO_Rk_rolling_10_home', 'AdjD_rolling_10_home',
       'AdjD_Rk_rolling_10_home', 'AdjT_rolling_10_home',
       'AdjT_Rk_rolling_10_home', 'Rk_rolling_20_home',
       'AdjEM_rolling_20_home', 'AdjO_rolling_20_home',
       'AdjO_Rk_rolling_20_home', 'AdjD_rolling_20_home',
       'AdjD_Rk_rolling_20_home', 'AdjT_rolling_20_home',
       'AdjT_Rk_rolling_20_home', 'Rk_away', 'Conf_away',
       'AdjEM_away', 'AdjO_away', 'AdjO_Rk_away', 'AdjD_away',
       'AdjD_Rk_away', 'AdjT_away', 'AdjT_Rk_away',
       'Rk_rolling_1_away', 'AdjEM_rolling_1_away', 'AdjO_rolling_1_away',
       'AdjO_Rk_rolling_1_away', 'AdjD_rolling_1_away',
       'AdjD_Rk_rolling_1_away', 'AdjT_rolling_1_away',
       'AdjT_Rk_rolling_1_away', 'Rk_rolling_3_away',
       'AdjEM_rolling_3_away', 'AdjO_rolling_3_away',
       'AdjO_Rk_rolling_3_away', 'AdjD_rolling_3_away',
       'AdjD_Rk_rolling_3_away', 'AdjT_rolling_3_away',
       'AdjT_Rk_rolling_3_away', 'Rk_rolling_5_away',
       'AdjEM_rolling_5_away', 'AdjO_rolling_5_away',
       'AdjO_Rk_rolling_5_away', 'AdjD_rolling_5_away',
       'AdjD_Rk_rolling_5_away', 'AdjT_rolling_5_away',
       'AdjT_Rk_rolling_5_away', 'Rk_rolling_10_away',
       'AdjEM_rolling_10_away', 'AdjO_rolling_10_away',
       'AdjO_Rk_rolling_10_away', 'AdjD_rolling_10_away',
       'AdjD_Rk_rolling_10_away', 'AdjT_rolling_10_away',
       'AdjT_Rk_rolling_10_away', 'Rk_rolling_20_away',
       'AdjEM_rolling_20_away', 'AdjO_rolling_20_away',
       'AdjO_Rk_rolling_20_away', 'AdjD_rolling_20_away',
       'AdjD_Rk_rolling_20_away', 'AdjT_rolling_20_away',
       'AdjT_Rk_rolling_20_away',  'home_sos',
       'away_sos', 'home_days_since_last_game',
       'home_rolling_avg_score_1', 'home_rolling_avg_score_3',
       'home_rolling_avg_score_7', 'home_rolling_sos_1',
       'home_rolling_sos_3', 'home_rolling_sos_7',
       'home_rolling_avg_score_allowed_1',
       'home_rolling_avg_score_allowed_3',
       'home_rolling_avg_score_allowed_7',
       'home_rolling_opp_score_rank_1', 'home_rolling_opp_score_rank_3',
       'home_rolling_opp_score_rank_7', 'away_days_since_last_game',
       'away_rolling_avg_score_1', 'away_rolling_avg_score_3',
       'away_rolling_avg_score_7', 'away_rolling_sos_1',
       'away_rolling_sos_3', 'away_rolling_sos_7',
       'away_rolling_avg_score_allowed_1',
       'away_rolling_avg_score_allowed_3',
       'away_rolling_avg_score_allowed_7',
       'away_rolling_opp_score_rank_1', 'away_rolling_opp_score_rank_3',
       'away_rolling_opp_score_rank_7']]

    # Encode categorical columns
    for cat_col in categorical_columns:
        le = LabelEncoder()
        model_df[cat_col] = le.fit_transform(df[cat_col])

    # Ensure the dataframe is sorted by the "date" column
    model_df['date'] = pd.to_datetime(df['Date'])  # Convert to datetime if not already
    model_df = model_df.sort_values(by='date')

    # Define the split ratio
    test_ratio = 0.2  # 20% of the data will be used for testing
    split_index = int(len(model_df) * (1 - test_ratio))

    # Split data into training and testing sets
    train_data = model_df.iloc[:split_index]
    test_data = model_df.iloc[split_index:]

    # Separate features and target
    X_train = train_data.drop(columns=['date', 'Date', target_column])
    y_train = train_data[target_column]

    X_test = test_data.drop(columns=['date', 'Date', target_column])
    y_test = test_data[target_column]

    def objective_xgb(trial):
        param = {
            'objective': 'binary:logistic',
            'eval_metric': 'logloss',
            'max_depth': trial.suggest_int('max_depth', 3, 10),
            'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 0.3),
            'n_estimators': trial.suggest_int('n_estimators', 100, 1500),
            'min_child_weight': trial.suggest_int('min_child_weight', 1, 10),
            'subsample': trial.suggest_float('subsample', 0.5, 1.0),
            'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
            'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 5.0),
            'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 5.0),
        }

        # Train XGBoost model
        model = xgb.XGBClassifier(**param, use_label_encoder=False)
        model.fit(X_train, y_train, eval_set=[(X_test, y_test)], early_stopping_rounds=10, verbose=False)

        # Evaluate the model using AUC as the optimization metric
        y_pred_proba = model.predict_proba(X_test)[:, 1]
        auc = roc_auc_score(y_test, y_pred_proba)
        return 1 - auc  # Minimize (1 - AUC)

    # Optimize XGBoost with Optuna
    study_xgb = optuna.create_study(direction='minimize')
    study_xgb.optimize(objective_xgb, n_trials=15)
    print(f"Best XGBoost parameters for {target_column}: {study_xgb.best_params}")

    # Train the final XGBoost model with the best parameters
    best_xgb = xgb.XGBClassifier(**study_xgb.best_params, use_label_encoder=False)
    best_xgb.fit(X_train, y_train)
    y_pred = best_xgb.predict(X_test)
    y_pred_proba = best_xgb.predict_proba(X_test)[:, 1]

    # Calculate metrics
    auc = roc_auc_score(y_test, y_pred_proba)
    accuracy = accuracy_score(y_test, y_pred)
    f1 = f1_score(y_test, y_pred)
    mcc = matthews_corrcoef(y_test, y_pred)

    # Display metrics
    print(f"Metrics for {target_column}:")
    print(f"AUC: {auc:.4f}")
    print(f"Accuracy: {accuracy:.4f}")
    print(f"F1 Score: {f1:.4f}")
    print(f"MCC: {mcc:.4f}")

    # Save the final model
    model_path = f"xgb_models/{target_column}_best_model.joblib"
    joblib.dump(best_xgb, model_path)
    print(f"Model saved to {model_path}")

/var/folders/0b/h0zc244107jg60tttkl4r0kw0000gn/T/ipykernel_501/879177568.py:84: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  model_df[cat_col] = le.fit_transform(df[cat_col])
/var/folders/0b/h0zc244107jg60tttkl4r0kw0000gn/T/ipykernel_501/879177568.py:87: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  model_df['date'] = pd.to_datetime(df['Date'])  # Convert to datetime if not already
[I 2024-11-25 08:50:15,847] A new study created in memory with name: no-name-ea40788b-c51a-436a-bb40-d599880170e9
/var/folders

Best XGBoost parameters for home_win: {'max_depth': 4, 'learning_rate': 0.010829648023162497, 'n_estimators': 1106, 'min_child_weight': 6, 'subsample': 0.5067993980450405, 'colsample_bytree': 0.5164111685918681, 'reg_alpha': 0.8945854676306653, 'reg_lambda': 4.788248512991332}
Metrics for home_win:
AUC: 0.7747
Accuracy: 0.6965
F1 Score: 0.6975
MCC: 0.3931
Model saved to xgb_models/home_win_best_model.joblib


/var/folders/0b/h0zc244107jg60tttkl4r0kw0000gn/T/ipykernel_501/879177568.py:84: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  model_df[cat_col] = le.fit_transform(df[cat_col])
/var/folders/0b/h0zc244107jg60tttkl4r0kw0000gn/T/ipykernel_501/879177568.py:87: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  model_df['date'] = pd.to_datetime(df['Date'])  # Convert to datetime if not already
[I 2024-11-25 08:58:15,362] A new study created in memory with name: no-name-b71aafd1-aa0f-4866-9026-100bdf76f1ba
/var/folders

Best XGBoost parameters for away_win: {'max_depth': 4, 'learning_rate': 0.010794438699945744, 'n_estimators': 1424, 'min_child_weight': 1, 'subsample': 0.5060593858397434, 'colsample_bytree': 0.9061760984354007, 'reg_alpha': 2.043618456321129, 'reg_lambda': 1.5824029012988672}
Metrics for away_win:
AUC: 0.7735
Accuracy: 0.6955
F1 Score: 0.6950
MCC: 0.3911
Model saved to xgb_models/away_win_best_model.joblib


## ADABOOST

In [9]:
import os
import pandas as pd
import joblib
from sklearn.ensemble import AdaBoostClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import roc_auc_score, accuracy_score, f1_score
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
import optuna

os.makedirs("adaboost_models", exist_ok=True)


for target_column in ['home_win', 'away_win']:
    categorical_columns = ['Conf_home', 'Conf_away']  # Update to actual categorical columns

    # Prepare data
    model_df = df[[target_column, 'Date','Rk_home','Conf_home', 'AdjEM_home', 'AdjO_home',
       'AdjO_Rk_home', 'AdjD_home', 'AdjD_Rk_home', 'AdjT_home',
       'AdjT_Rk_home', 'Rk_rolling_1_home',
       'AdjEM_rolling_1_home', 'AdjO_rolling_1_home',
       'AdjO_Rk_rolling_1_home', 'AdjD_rolling_1_home',
       'AdjD_Rk_rolling_1_home', 'AdjT_rolling_1_home',
       'AdjT_Rk_rolling_1_home', 'Rk_rolling_3_home',
       'AdjEM_rolling_3_home', 'AdjO_rolling_3_home',
       'AdjO_Rk_rolling_3_home', 'AdjD_rolling_3_home',
       'AdjD_Rk_rolling_3_home', 'AdjT_rolling_3_home',
       'AdjT_Rk_rolling_3_home', 'Rk_rolling_5_home',
       'AdjEM_rolling_5_home', 'AdjO_rolling_5_home',
       'AdjO_Rk_rolling_5_home', 'AdjD_rolling_5_home',
       'AdjD_Rk_rolling_5_home', 'AdjT_rolling_5_home',
       'AdjT_Rk_rolling_5_home', 'Rk_rolling_10_home',
       'AdjEM_rolling_10_home', 'AdjO_rolling_10_home',
       'AdjO_Rk_rolling_10_home', 'AdjD_rolling_10_home',
       'AdjD_Rk_rolling_10_home', 'AdjT_rolling_10_home',
       'AdjT_Rk_rolling_10_home', 'Rk_rolling_20_home',
       'AdjEM_rolling_20_home', 'AdjO_rolling_20_home',
       'AdjO_Rk_rolling_20_home', 'AdjD_rolling_20_home',
       'AdjD_Rk_rolling_20_home', 'AdjT_rolling_20_home',
       'AdjT_Rk_rolling_20_home', 'Rk_away', 'Conf_away',
       'AdjEM_away', 'AdjO_away', 'AdjO_Rk_away', 'AdjD_away',
       'AdjD_Rk_away', 'AdjT_away', 'AdjT_Rk_away',
       'Rk_rolling_1_away', 'AdjEM_rolling_1_away', 'AdjO_rolling_1_away',
       'AdjO_Rk_rolling_1_away', 'AdjD_rolling_1_away',
       'AdjD_Rk_rolling_1_away', 'AdjT_rolling_1_away',
       'AdjT_Rk_rolling_1_away', 'Rk_rolling_3_away',
       'AdjEM_rolling_3_away', 'AdjO_rolling_3_away',
       'AdjO_Rk_rolling_3_away', 'AdjD_rolling_3_away',
       'AdjD_Rk_rolling_3_away', 'AdjT_rolling_3_away',
       'AdjT_Rk_rolling_3_away', 'Rk_rolling_5_away',
       'AdjEM_rolling_5_away', 'AdjO_rolling_5_away',
       'AdjO_Rk_rolling_5_away', 'AdjD_rolling_5_away',
       'AdjD_Rk_rolling_5_away', 'AdjT_rolling_5_away',
       'AdjT_Rk_rolling_5_away', 'Rk_rolling_10_away',
       'AdjEM_rolling_10_away', 'AdjO_rolling_10_away',
       'AdjO_Rk_rolling_10_away', 'AdjD_rolling_10_away',
       'AdjD_Rk_rolling_10_away', 'AdjT_rolling_10_away',
       'AdjT_Rk_rolling_10_away', 'Rk_rolling_20_away',
       'AdjEM_rolling_20_away', 'AdjO_rolling_20_away',
       'AdjO_Rk_rolling_20_away', 'AdjD_rolling_20_away',
       'AdjD_Rk_rolling_20_away', 'AdjT_rolling_20_away',
       'AdjT_Rk_rolling_20_away',  'home_sos',
       'away_sos', 'home_days_since_last_game',
       'home_rolling_avg_score_1', 'home_rolling_avg_score_3',
       'home_rolling_avg_score_7', 'home_rolling_sos_1',
       'home_rolling_sos_3', 'home_rolling_sos_7',
       'home_rolling_avg_score_allowed_1',
       'home_rolling_avg_score_allowed_3',
       'home_rolling_avg_score_allowed_7',
       'home_rolling_opp_score_rank_1', 'home_rolling_opp_score_rank_3',
       'home_rolling_opp_score_rank_7', 'away_days_since_last_game',
       'away_rolling_avg_score_1', 'away_rolling_avg_score_3',
       'away_rolling_avg_score_7', 'away_rolling_sos_1',
       'away_rolling_sos_3', 'away_rolling_sos_7',
       'away_rolling_avg_score_allowed_1',
       'away_rolling_avg_score_allowed_3',
       'away_rolling_avg_score_allowed_7',
       'away_rolling_opp_score_rank_1', 'away_rolling_opp_score_rank_3',
       'away_rolling_opp_score_rank_7']]

    # Encode categorical columns
    for cat_col in categorical_columns:
        le = LabelEncoder()
        model_df.loc[:, cat_col] = le.fit_transform(df[cat_col])

    model_df.loc[:, 'Date'] = pd.to_datetime(model_df['Date'])

    # Sort the dataframe by date in ascending order
    model_df = model_df.sort_values(by='Date').reset_index(drop=True)

    # Calculate the index for the 80% split
    split_index = int(len(model_df) * 0.8)

    # Split the data into training and testing sets
    train_data = model_df.iloc[:split_index]
    test_data = model_df.iloc[split_index:]

    # Separate features and target
    X_train = train_data.drop(columns=['Date', target_column])
    y_train = train_data[target_column]

    X_test = test_data.drop(columns=['Date', target_column])
    y_test = test_data[target_column]

    # Define Optuna objective function for AdaBoost
    def objective_adaboost(trial):
        param = {
            'n_estimators': trial.suggest_int('n_estimators', 50, 500),
            'learning_rate': trial.suggest_float('learning_rate', 0.01, 1.0, log=True),
            'base_estimator__max_depth': trial.suggest_int('max_depth', 1, 5),
        }

        # Define AdaBoost with a DecisionTree base estimator
        base_estimator = DecisionTreeClassifier(max_depth=param['base_estimator__max_depth'])
        model = AdaBoostClassifier(base_estimator=base_estimator,
                                   n_estimators=param['n_estimators'],
                                   learning_rate=param['learning_rate'])

        model.fit(X_train, y_train)
        y_pred_proba = model.predict_proba(X_test)[:, 1]

        # Use ROC AUC as the optimization metric
        auc = roc_auc_score(y_test, y_pred_proba)
        return auc

    # Optimize AdaBoost with Optuna
    study_adaboost = optuna.create_study(direction='maximize')
    study_adaboost.optimize(objective_adaboost, n_trials=5)
    print(f"Best AdaBoost parameters for {target_column}: {study_adaboost.best_params}")

    # Train the best AdaBoost model with optimized parameters
    best_params = study_adaboost.best_params
    best_base_estimator = DecisionTreeClassifier(max_depth=best_params['base_estimator__max_depth'])
    best_adaboost = AdaBoostClassifier(base_estimator=best_base_estimator,
                                       n_estimators=best_params['n_estimators'],
                                       learning_rate=best_params['learning_rate'])
    best_adaboost.fit(X_train, y_train)

    # Predict and evaluate
    y_pred = best_adaboost.predict(X_test)
    y_pred_proba = best_adaboost.predict_proba(X_test)[:, 1]

    # Define a function to calculate and display metrics
    def display_metrics(y_true, y_pred, y_pred_proba, model_name):
        auc = roc_auc_score(y_true, y_pred_proba)
        accuracy = accuracy_score(y_true, y_pred)
        f1 = f1_score(y_true, y_pred)
        print(f"{model_name} AUC: {auc:.4f}")
        print(f"{model_name} Accuracy: {accuracy:.4f}")
        print(f"{model_name} F1 Score: {f1:.4f}")

    # Display metrics for the AdaBoost model
    display_metrics(y_test, y_pred, y_pred_proba, "AdaBoost")

    # Save the final best model for this target column
    best_model_filename = f"adaboost_models/{target_column}_best_model.joblib"
    joblib.dump(best_adaboost, best_model_filename)


/var/folders/0b/h0zc244107jg60tttkl4r0kw0000gn/T/ipykernel_91658/4279417457.py:84: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  model_df.loc[:, cat_col] = le.fit_transform(df[cat_col])
/var/folders/0b/h0zc244107jg60tttkl4r0kw0000gn/T/ipykernel_91658/4279417457.py:84: FutureWarning: In a future version, `df.iloc[:, i] = newvals` will attempt to set the values inplace instead of always setting a new array. To retain the old behavior, use either `df[df.columns[i]] = newvals` or, if columns are non-unique, `df.isetitem(i, newvals)`
  model_df.loc[:, cat_col] = le.fit_transform(df[cat_col])
/var/folders/0b/h0zc244107jg60tttkl4r0kw0000gn/T/ipykernel_91658/4279417457.py:86: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from 

KeyboardInterrupt: 

In [13]:
import pandas as pd
from sklearn.ensemble import AdaBoostClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.metrics import roc_auc_score, accuracy_score, f1_score
from sklearn.model_selection import train_test_split

# Sample data preparation
model_df = df[['home_win','Date','Rk_home','Conf_home', 'AdjEM_home', 'AdjO_home',
       'AdjO_Rk_home', 'AdjD_home', 'AdjD_Rk_home', 'AdjT_home',
       'AdjT_Rk_home', 'Rk_rolling_1_home',
       'AdjEM_rolling_1_home', 'AdjO_rolling_1_home',
       'AdjO_Rk_rolling_1_home', 'AdjD_rolling_1_home',
       'AdjD_Rk_rolling_1_home', 'AdjT_rolling_1_home',
       'AdjT_Rk_rolling_1_home', 'Rk_rolling_3_home',
       'AdjEM_rolling_3_home', 'AdjO_rolling_3_home',
       'AdjO_Rk_rolling_3_home', 'AdjD_rolling_3_home',
       'AdjD_Rk_rolling_3_home', 'AdjT_rolling_3_home',
       'AdjT_Rk_rolling_3_home', 'Rk_rolling_5_home',
       'AdjEM_rolling_5_home', 'AdjO_rolling_5_home',
       'AdjO_Rk_rolling_5_home', 'AdjD_rolling_5_home',
       'AdjD_Rk_rolling_5_home', 'AdjT_rolling_5_home',
       'AdjT_Rk_rolling_5_home', 'Rk_rolling_10_home',
       'AdjEM_rolling_10_home', 'AdjO_rolling_10_home',
       'AdjO_Rk_rolling_10_home', 'AdjD_rolling_10_home',
       'AdjD_Rk_rolling_10_home', 'AdjT_rolling_10_home',
       'AdjT_Rk_rolling_10_home', 'Rk_rolling_20_home',
       'AdjEM_rolling_20_home', 'AdjO_rolling_20_home',
       'AdjO_Rk_rolling_20_home', 'AdjD_rolling_20_home',
       'AdjD_Rk_rolling_20_home', 'AdjT_rolling_20_home',
       'AdjT_Rk_rolling_20_home', 'Rk_away', 'Conf_away',
       'AdjEM_away', 'AdjO_away', 'AdjO_Rk_away', 'AdjD_away',
       'AdjD_Rk_away', 'AdjT_away', 'AdjT_Rk_away',
       'Rk_rolling_1_away', 'AdjEM_rolling_1_away', 'AdjO_rolling_1_away',
       'AdjO_Rk_rolling_1_away', 'AdjD_rolling_1_away',
       'AdjD_Rk_rolling_1_away', 'AdjT_rolling_1_away',
       'AdjT_Rk_rolling_1_away', 'Rk_rolling_3_away',
       'AdjEM_rolling_3_away', 'AdjO_rolling_3_away',
       'AdjO_Rk_rolling_3_away', 'AdjD_rolling_3_away',
       'AdjD_Rk_rolling_3_away', 'AdjT_rolling_3_away',
       'AdjT_Rk_rolling_3_away', 'Rk_rolling_5_away',
       'AdjEM_rolling_5_away', 'AdjO_rolling_5_away',
       'AdjO_Rk_rolling_5_away', 'AdjD_rolling_5_away',
       'AdjD_Rk_rolling_5_away', 'AdjT_rolling_5_away',
       'AdjT_Rk_rolling_5_away', 'Rk_rolling_10_away',
       'AdjEM_rolling_10_away', 'AdjO_rolling_10_away',
       'AdjO_Rk_rolling_10_away', 'AdjD_rolling_10_away',
       'AdjD_Rk_rolling_10_away', 'AdjT_rolling_10_away',
       'AdjT_Rk_rolling_10_away', 'Rk_rolling_20_away',
       'AdjEM_rolling_20_away', 'AdjO_rolling_20_away',
       'AdjO_Rk_rolling_20_away', 'AdjD_rolling_20_away',
       'AdjD_Rk_rolling_20_away', 'AdjT_rolling_20_away',
       'AdjT_Rk_rolling_20_away',  'home_sos',
       'away_sos', 'home_days_since_last_game',
       'home_rolling_avg_score_1', 'home_rolling_avg_score_3',
       'home_rolling_avg_score_7', 'home_rolling_sos_1',
       'home_rolling_sos_3', 'home_rolling_sos_7',
       'home_rolling_avg_score_allowed_1',
       'home_rolling_avg_score_allowed_3',
       'home_rolling_avg_score_allowed_7',
       'home_rolling_opp_score_rank_1', 'home_rolling_opp_score_rank_3',
       'home_rolling_opp_score_rank_7', 'away_days_since_last_game',
       'away_rolling_avg_score_1', 'away_rolling_avg_score_3',
       'away_rolling_avg_score_7', 'away_rolling_sos_1',
       'away_rolling_sos_3', 'away_rolling_sos_7',
       'away_rolling_avg_score_allowed_1',
       'away_rolling_avg_score_allowed_3',
       'away_rolling_avg_score_allowed_7',
       'away_rolling_opp_score_rank_1', 'away_rolling_opp_score_rank_3',
       'away_rolling_opp_score_rank_7']]  # Adjust columns as needed
categorical_columns = ['Conf_home', 'Conf_away']

# Encode categorical columns
for cat_col in categorical_columns:
    le = LabelEncoder()
    model_df[cat_col] = le.fit_transform(model_df[cat_col])

# Convert 'Date' column to datetime
model_df['Date'] = pd.to_datetime(model_df['Date'])
model_df = model_df.sort_values(by='Date').reset_index(drop=True)

# Train-test split
split_index = int(len(model_df) * 0.8)
train_data = model_df.iloc[:split_index]
test_data = model_df.iloc[split_index:]
X_train = train_data.drop(columns=['Date', 'home_win'])
y_train = train_data['home_win']
X_test = test_data.drop(columns=['Date', 'home_win'])
y_test = test_data['home_win']

# Standardize features
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Train AdaBoost model
base_estimator = DecisionTreeClassifier(max_depth=3)
adaboost = AdaBoostClassifier(base_estimator=base_estimator, n_estimators=100, learning_rate=0.1)
adaboost.fit(X_train, y_train)

# Save the trained model
model_path = "adaboost_models/home_win_adaboost_model.joblib"
joblib.dump(adaboost, model_path)
print(f"AdaBoost model saved to {model_path}")

# Predict and evaluate
y_pred = adaboost.predict(X_test)
y_pred_proba = adaboost.predict_proba(X_test)[:, 1]

# Performance metrics
auc = roc_auc_score(y_test, y_pred_proba)
accuracy = accuracy_score(y_test, y_pred)
f1 = f1_score(y_test, y_pred)

print(f"AdaBoost AUC: {auc:.4f}")
print(f"AdaBoost Accuracy: {accuracy:.4f}")
print(f"AdaBoost F1 Score: {f1:.4f}")


/var/folders/0b/h0zc244107jg60tttkl4r0kw0000gn/T/ipykernel_91658/425588026.py:76: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  model_df[cat_col] = le.fit_transform(model_df[cat_col])
/var/folders/0b/h0zc244107jg60tttkl4r0kw0000gn/T/ipykernel_91658/425588026.py:79: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  model_df['Date'] = pd.to_datetime(model_df['Date'])
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/ensemble/_base.py:166: FutureWarning: `base_estimator` was r

AdaBoost model saved to adaboost_models/home_win_adaboost_model.joblib
AdaBoost AUC: 0.7729
AdaBoost Accuracy: 0.6973
AdaBoost F1 Score: 0.6971


In [14]:
import pandas as pd
from sklearn.ensemble import AdaBoostClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.metrics import roc_auc_score, accuracy_score, f1_score
from sklearn.model_selection import train_test_split

# Sample data preparation
model_df = df[['away_win','Date','Rk_home','Conf_home', 'AdjEM_home', 'AdjO_home',
       'AdjO_Rk_home', 'AdjD_home', 'AdjD_Rk_home', 'AdjT_home',
       'AdjT_Rk_home', 'Rk_rolling_1_home',
       'AdjEM_rolling_1_home', 'AdjO_rolling_1_home',
       'AdjO_Rk_rolling_1_home', 'AdjD_rolling_1_home',
       'AdjD_Rk_rolling_1_home', 'AdjT_rolling_1_home',
       'AdjT_Rk_rolling_1_home', 'Rk_rolling_3_home',
       'AdjEM_rolling_3_home', 'AdjO_rolling_3_home',
       'AdjO_Rk_rolling_3_home', 'AdjD_rolling_3_home',
       'AdjD_Rk_rolling_3_home', 'AdjT_rolling_3_home',
       'AdjT_Rk_rolling_3_home', 'Rk_rolling_5_home',
       'AdjEM_rolling_5_home', 'AdjO_rolling_5_home',
       'AdjO_Rk_rolling_5_home', 'AdjD_rolling_5_home',
       'AdjD_Rk_rolling_5_home', 'AdjT_rolling_5_home',
       'AdjT_Rk_rolling_5_home', 'Rk_rolling_10_home',
       'AdjEM_rolling_10_home', 'AdjO_rolling_10_home',
       'AdjO_Rk_rolling_10_home', 'AdjD_rolling_10_home',
       'AdjD_Rk_rolling_10_home', 'AdjT_rolling_10_home',
       'AdjT_Rk_rolling_10_home', 'Rk_rolling_20_home',
       'AdjEM_rolling_20_home', 'AdjO_rolling_20_home',
       'AdjO_Rk_rolling_20_home', 'AdjD_rolling_20_home',
       'AdjD_Rk_rolling_20_home', 'AdjT_rolling_20_home',
       'AdjT_Rk_rolling_20_home', 'Rk_away', 'Conf_away',
       'AdjEM_away', 'AdjO_away', 'AdjO_Rk_away', 'AdjD_away',
       'AdjD_Rk_away', 'AdjT_away', 'AdjT_Rk_away',
       'Rk_rolling_1_away', 'AdjEM_rolling_1_away', 'AdjO_rolling_1_away',
       'AdjO_Rk_rolling_1_away', 'AdjD_rolling_1_away',
       'AdjD_Rk_rolling_1_away', 'AdjT_rolling_1_away',
       'AdjT_Rk_rolling_1_away', 'Rk_rolling_3_away',
       'AdjEM_rolling_3_away', 'AdjO_rolling_3_away',
       'AdjO_Rk_rolling_3_away', 'AdjD_rolling_3_away',
       'AdjD_Rk_rolling_3_away', 'AdjT_rolling_3_away',
       'AdjT_Rk_rolling_3_away', 'Rk_rolling_5_away',
       'AdjEM_rolling_5_away', 'AdjO_rolling_5_away',
       'AdjO_Rk_rolling_5_away', 'AdjD_rolling_5_away',
       'AdjD_Rk_rolling_5_away', 'AdjT_rolling_5_away',
       'AdjT_Rk_rolling_5_away', 'Rk_rolling_10_away',
       'AdjEM_rolling_10_away', 'AdjO_rolling_10_away',
       'AdjO_Rk_rolling_10_away', 'AdjD_rolling_10_away',
       'AdjD_Rk_rolling_10_away', 'AdjT_rolling_10_away',
       'AdjT_Rk_rolling_10_away', 'Rk_rolling_20_away',
       'AdjEM_rolling_20_away', 'AdjO_rolling_20_away',
       'AdjO_Rk_rolling_20_away', 'AdjD_rolling_20_away',
       'AdjD_Rk_rolling_20_away', 'AdjT_rolling_20_away',
       'AdjT_Rk_rolling_20_away',  'home_sos',
       'away_sos', 'home_days_since_last_game',
       'home_rolling_avg_score_1', 'home_rolling_avg_score_3',
       'home_rolling_avg_score_7', 'home_rolling_sos_1',
       'home_rolling_sos_3', 'home_rolling_sos_7',
       'home_rolling_avg_score_allowed_1',
       'home_rolling_avg_score_allowed_3',
       'home_rolling_avg_score_allowed_7',
       'home_rolling_opp_score_rank_1', 'home_rolling_opp_score_rank_3',
       'home_rolling_opp_score_rank_7', 'away_days_since_last_game',
       'away_rolling_avg_score_1', 'away_rolling_avg_score_3',
       'away_rolling_avg_score_7', 'away_rolling_sos_1',
       'away_rolling_sos_3', 'away_rolling_sos_7',
       'away_rolling_avg_score_allowed_1',
       'away_rolling_avg_score_allowed_3',
       'away_rolling_avg_score_allowed_7',
       'away_rolling_opp_score_rank_1', 'away_rolling_opp_score_rank_3',
       'away_rolling_opp_score_rank_7']]  # Adjust columns as needed
categorical_columns = ['Conf_home', 'Conf_away']

# Encode categorical columns
for cat_col in categorical_columns:
    le = LabelEncoder()
    model_df[cat_col] = le.fit_transform(model_df[cat_col])

# Convert 'Date' column to datetime
model_df['Date'] = pd.to_datetime(model_df['Date'])
model_df = model_df.sort_values(by='Date').reset_index(drop=True)

# Train-test split
split_index = int(len(model_df) * 0.8)
train_data = model_df.iloc[:split_index]
test_data = model_df.iloc[split_index:]
X_train = train_data.drop(columns=['Date', 'away_win'])
y_train = train_data['away_win']
X_test = test_data.drop(columns=['Date', 'away_win'])
y_test = test_data['away_win']

# Standardize features
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Train AdaBoost model
base_estimator = DecisionTreeClassifier(max_depth=3)
adaboost = AdaBoostClassifier(base_estimator=base_estimator, n_estimators=100, learning_rate=0.1)
adaboost.fit(X_train, y_train)

# Save the trained model
model_path = "adaboost_models/away_win_adaboost_model.joblib"
joblib.dump(adaboost, model_path)
print(f"AdaBoost model saved to {model_path}")

# Predict and evaluate
y_pred = adaboost.predict(X_test)
y_pred_proba = adaboost.predict_proba(X_test)[:, 1]

# Performance metrics
auc = roc_auc_score(y_test, y_pred_proba)
accuracy = accuracy_score(y_test, y_pred)
f1 = f1_score(y_test, y_pred)

print(f"AdaBoost AUC: {auc:.4f}")
print(f"AdaBoost Accuracy: {accuracy:.4f}")
print(f"AdaBoost F1 Score: {f1:.4f}")

/var/folders/0b/h0zc244107jg60tttkl4r0kw0000gn/T/ipykernel_91658/3786382773.py:76: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  model_df[cat_col] = le.fit_transform(model_df[cat_col])
/var/folders/0b/h0zc244107jg60tttkl4r0kw0000gn/T/ipykernel_91658/3786382773.py:79: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  model_df['Date'] = pd.to_datetime(model_df['Date'])
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/ensemble/_base.py:166: FutureWarning: `base_estimator` was

AdaBoost model saved to adaboost_models/away_win_adaboost_model.joblib
AdaBoost AUC: 0.7727
AdaBoost Accuracy: 0.6972
AdaBoost F1 Score: 0.6974
